# Gitcoin Grants 13 Sybil Detection Report

## Preparation

In [1]:
import pandas as pd
import json
import plotly.express as px
import numpy as np
import scipy.stats as st
from util import open_largest_file_in_zip

### Load Aggregate Result

In [2]:
path = '../private_data/gr13_report/csv_output-20220330-210922.csv.zip'
output_df = open_largest_file_in_zip(path, pd.read_csv).set_index('handle')
output_df.head(2)

aggregate_score  prediction_score  evaluation_score  \
handle                                                            
yuxi71415               0.0          0.137216               NaN   
kerwin6574              0.0          0.474703               NaN   

            heuristic_score  create_distance  update_distance  public_repos  \
handle                                                                        
yuxi71415               NaN           -259.0           -252.0           0.0   
kerwin6574              NaN             13.0             13.0           0.0   

            followers  following  bio_length  amount_in_usdt_median  \
handle                                                                
yuxi71415         0.0        0.0         0.0               1.032661   
kerwin6574        0.0        0.0         0.0               1.100000   

            amount_in_usdt_std  amount_in_usdt_std_per_count  \
handle                                                         
yuxi71415             0.231365                      0.012177   
kerwin6574            0.090374                      0.003012   

            amount_to_gitcoin_ratio  contrib_count  eth_share token  
handle                                                               
yuxi71415                    0.0013           19.0   0.052632   ETH  
kerwin6574                   0.0500           30.0   0.000000  USDC

### Load Contributions

In [3]:
from tempfile import NamedTemporaryFile

def load_hdf(fid):
    with NamedTemporaryFile() as tmp:
        tmp.write(fid.read())
        return pd.read_hdf(tmp.name, 'metabase')

path = '../private_data/gr13_report/raw_data-20220328-181649.hdf5.zip'
contribs_df = open_largest_file_in_zip(path, load_hdf)
contribs_df.head(2)


created_on                      modified_on  \
0 2022-03-09 00:48:22.679256+00:00 2022-03-09 01:10:31.787229+00:00   
1 2022-03-09 00:48:27.536815+00:00 2022-03-09 01:10:31.370439+00:00   

   profile_for_clr_id  success                              wallet_address  \
0              332891     True  0x69509364652015dd60dfe20a1dbfbe548d70e68d   
1              332891     True  0x69509364652015dd60dfe20a1dbfbe548d70e68d   

      handle  raw_amount_in_token  amount_in_token  \
0  hsutaiwan                 10.0             10.0   
1  hsutaiwan                 10.0             10.0   

   amount_to_gitcoin_in_token  amount_in_usdt token        ip_addr  
0                         0.5            10.0   DAI  49.217.64.131  
1                         0.5            10.0   DAI  49.217.64.131

### Load Human Flags

In [4]:
path = '../private_data/gr13_report/human_flags-20220328-183749.json.zip'
human_flags = open_largest_file_in_zip(path, json.load)

def eval_sheet_to_df(sheet, sheet_data):
    eval_round = sheet.split("HES_")[-1][-13:]
    evaluator = sheet.split("HES_")[0]
    eval_df = (pd.DataFrame
                 .from_dict(human_flags[sheet], orient='index')
                 .reset_index()
                 .rename(columns={'index': 'handle'})
                 .assign(sheet=sheet)
                 .assign(eval_round=eval_round)
                 .assign(evaluator=evaluator)
              )
    return eval_df


def evaluation_score_rule(d: dict) -> float:
    """
    Returns a value of [0, 1] OR **nan** for each user.
    """
    v_1 = d['is_sybil'].lower().strip()
    v_2 = d['answer_confidence'].lower().strip()

    if v_1 in {'t', 'f'} and v_2 in {'low', 'so-so', 'high'}:
        if v_1 == 't':
            if v_2 == 'low':
                return 3 / 5
            elif v_2 == 'so-so':
                return 4 / 5
            elif v_2 == 'high':
                return 5 / 5
            else:
                return 4 / 5
        else:
            if v_2 == 'low':
                return 2 / 5
            elif v_2 == 'so-so':
                return 1 / 5
            elif v_2 == 'high':
                return 0 / 5
            else:
                return 1 / 5       
    else:
        return np.nan
    
    
human_flags_df = (pd.concat([eval_sheet_to_df(sheet, sheet_data)
                             for (sheet, sheet_data)
                             in human_flags.items()])
                    .set_index(['eval_round', 'evaluator', 'handle'])
                    .assign(evaluation_score=lambda df: df.apply(evaluation_score_rule, axis=1))
                    .query("eval_round != 'Squelches'")
                 )

human_flags_df.head(2)

is_sybil answer_confidence  \
eval_round    evaluator handle                                       
20220314-2343 Adebola_  connorpaca             T              High   
                        okeaguugochukwu        F              High   

                                                                                     notes  \
eval_round    evaluator handle                                                               
20220314-2343 Adebola_  connorpaca       New gitcoin and Github accounts, super low and...   
                        okeaguugochukwu  Gitcoin and Github account are not recent, wit...   

                                                                gitcoin_url  \
eval_round    evaluator handle                                                
20220314-2343 Adebola_  connorpaca            https://gitcoin.co/connorpaca   
                        okeaguugochukwu  https://gitcoin.co/okeaguugochukwu   

                                                                 github_url  \
eval_round    evaluator handle                                                
20220314-2343 Adebola_  connorpaca            https://github.com/connorpaca   
                        okeaguugochukwu  https://github.com/okeaguugochukwu   

                                                               sheet  \
eval_round    evaluator handle                                         
20220314-2343 Adebola_  connorpaca       Adebola_HES_0_20220314-2343   
                        okeaguugochukwu  Adebola_HES_0_20220314-2343   

                                         evaluation_score  
eval_round    evaluator handle                             
20220314-2343 Adebola_  connorpaca                    1.0  
                        okeaguugochukwu               0.0

## Analysis

### Sybil Incidence

In [5]:
print("---")
df = human_flags_df.assign(high_confidence_sybil=lambda df: df.evaluation_score > 0.9)
incidence_avg = df.high_confidence_sybil.mean()
n = len(df)
p = incidence_avg
incidence_ci = (st.binom.ppf(0.975, n, p) - st.binom.ppf(0.025, n, p)) / n

print(f"Estimated Sybil Incidence: {incidence_avg :.1%} +/- {incidence_ci :.1%}")

print("High Confidence Sybil Fraction per Round")
fig = px.bar(df.groupby("eval_round").high_confidence_sybil.mean(),
             labels={"value": "Estimated Sybil Incidence",
                     "eval_round": "Evaluation Round"})
fig.update_layout(yaxis_tickformat=',.0%') 
fig.show()

---
Estimated Sybil Incidence: 14.1% +/- 1.3%
High Confidence Sybil Fraction per Round


### Summary Statistics

##### Flagging Stats

In [6]:
COLS = {'aggregate_score',
        'prediction_score',
        'heuristic_score',
        'evaluation_score'}
fig_df = output_df.reset_index().melt(id_vars=['handle'], value_vars=COLS)

fig = px.histogram(fig_df,
                   x='value',
                   histnorm='percent',
                   title='Relative Distribution of Scores per User',
                   facet_col='variable',
                   nbins=24,
                   width=1000,
                   height=400)


fig.show()

In [7]:
fig = px.density_heatmap(output_df,
                         x='evaluation_score',
                         y='prediction_score',
                         facet_col='aggregate_score',
                         nbinsx=6,
                         nbinsy=20)
fig.show()

In [8]:
EVAL_THRESHOLD = 0.9
PRED_THRESHOLD = 0.7
print("---")

cond_1 = ~pd.isnull(output_df.evaluation_score)
val_1 = (cond_1).sum()
val_2 = (cond_1).mean()
print(f"Total users evaluated by humans: {cond_1.sum()} ({cond_1.mean() :.1%} of total)")
cond_1a = output_df.loc[cond_1, 'evaluation_score'] > EVAL_THRESHOLD
cond_1b = cond_1 & (~cond_1a)
print(f"~~threshold: {EVAL_THRESHOLD}~~")
print(f"Users marked as true by humans: {cond_1a.sum()} ({cond_1a.mean() :.1%})")
print(f"Users marked as false by humans: {cond_1b.sum()} ({1 - cond_1a.mean() :.1%})")
print("---")

cond_2 = ~pd.isnull(output_df.heuristic_score)
cond_2 = cond_2 & (~cond_1)
print(f"Total users evaluated by heuristics: {cond_2.sum()} ({cond_2.mean() :.1%} of total)")
cond_2a = output_df.loc[cond_2, 'heuristic_score'] > 0.5
cond_2b = cond_2 & (~cond_2a)
print(f"Users marked as true by heuristics: {cond_2a.sum()} ({cond_2a.mean() :.1%})")
print(f"Users marked as false by heuristics: {cond_2b.sum()} ({1 - cond_2a.mean() :.1%})")
print("---")


cond_3 = ~pd.isnull(output_df.prediction_score)
cond_3 = cond_3 &(~(cond_1 | cond_2))
print(f"Total users evaluated by algorithms: {cond_3.sum()} ({cond_3.mean() :.1%} of total)")
cond_3a = output_df.loc[cond_3, 'prediction_score'] > PRED_THRESHOLD
cond_3b = cond_3 & (~cond_3a)
print(f"~~threshold: {PRED_THRESHOLD}~~")
print(f"Users marked as true by algorithms: {cond_3a.sum()} ({cond_3a.mean() :.1%})")
print(f"Users marked as false by algorithms: {cond_3b.sum()} ({1 - cond_3a.mean() :.1%})")
print("---")

cond_4 = ~pd.isnull(output_df.aggregate_score)
print(f"Total users evaluated: {cond_4.sum()} ({cond_4.mean() :.1%} of total)")
cond_4a = output_df.loc[cond_4, 'aggregate_score'] > 0.5
cond_4b = cond_4 & (~cond_4a)
print(f"Users marked as true: {cond_4a.sum()} ({cond_4a.mean() :.1%})")
print(f"Users marked as false: {cond_4b.sum()} ({1 - cond_4a.mean() :.1%})")
print("---")

---
Total users evaluated by humans: 6405 (36.8% of total)
~~threshold: 0.9~~
Users marked as true by humans: 951 (14.8%)
Users marked as false by humans: 5454 (85.2%)
---
Total users evaluated by heuristics: 1180 (6.8% of total)
Users marked as true by heuristics: 1067 (90.4%)
Users marked as false by heuristics: 113 (9.6%)
---
Total users evaluated by algorithms: 9818 (56.4% of total)
~~threshold: 0.7~~
Users marked as true by algorithms: 53 (0.5%)
Users marked as false by algorithms: 9765 (99.5%)
---
Total users evaluated: 17403 (100.0% of total)
Users marked as true: 2071 (11.9%)
Users marked as false: 15332 (88.1%)
---


#### Sybil Impact

In [9]:
df = (contribs_df.assign(is_sybil=contribs_df.handle.map(cond_4a))
                 .dropna(subset=['is_sybil'])
                 .assign(kind='original')
                 .assign(match='t')
     )
SYBIL_HANDLE = 'SYBIL'

def f(d):
    d.loc[d.is_sybil, 'handle'] = SYBIL_HANDLE
    return d

modified_df = (df.copy()
                 .pipe(f)
                 .assign(kind='modified'))

# Key Assumption: set all sybil contributions as not-matching
modified_df.loc[modified_df.is_sybil.astype(bool), 'match'] = 'f'
modified_df.loc[~modified_df.is_sybil.astype(bool), 'match'] = 't'

removed_df = (df.copy()
                 .loc[modified_df.is_sybil, :]
                 .assign(kind='removed')
                 .assign(match='f'))

scenarios_df = pd.concat([df, modified_df, removed_df])
# Total Contributions

print(f"Total Contributions (original): {len(df)}")
print(f"Total Contributions (modified): {len(modified_df)}")
print(f"Total Contributions (removed): {len(removed_df)}")
print("___")
print(f"Matched Contributions (original): {sum(df.match == 't')}")
print(f"Matched Contributions (modified): {sum(modified_df.match == 't')}")
print(f"Matched Contributions (removed): {sum(removed_df.match == 't')}")

print(f"Change: {sum(df.match == 't') - sum(modified_df.match == 't')}")

# Some summary stats

GROUP_KEY = 'handle'

group_original = df.groupby(GROUP_KEY)
group_modified = modified_df.groupby(GROUP_KEY)
group_removed = removed_df.groupby(GROUP_KEY)


print(f"Total Contributors (original): {len(df.handle.unique())}")
print(f"Total Contributors (modified): {len(modified_df.handle.unique())}")
print(f"Total Contributors (removed): {len(removed_df.handle.unique())}")
print("---")

print(f"Sum of USDT Amount (original): {group_original.amount_in_usdt.sum().sum() :.2f}")
print(f"Sum of USDT Amount (removed): {group_removed.amount_in_usdt.sum().sum() :.2f}")
print("---")

print(f"Median of Median USDT Amount per User (original): {group_original.amount_in_usdt.median().median() :.2f}")
print(f"Median of Median USDT Amount per User (modified): {group_modified.amount_in_usdt.median().median() :.2f}")
print(f"Median of Median USDT Amount per User (removed): {group_removed.amount_in_usdt.median().median() :.2f}")
print("---")

print(f"Median Contribution Count per User (original): {group_original.amount_in_usdt.count().median() :.2f}")
print(f"Median Contribution Count per User (modified): {group_modified.amount_in_usdt.count().median() :.2f}")
print(f"Median Contribution Count per User (removed): {group_removed.amount_in_usdt.count().median() :.2f}")

print("---")

print(f"Mean Count per User (original): {group_original.amount_in_usdt.count().mean() :.2f}")
print(f"Mean Count per User (modified): {group_modified.amount_in_usdt.count().mean() :.2f}")
print(f"Mean Count per User (removed): {group_removed.amount_in_usdt.count().mean() :.2f}")
print("---")

COLS = {'amount_in_usdt', 'kind', 'handle'}
grouper = scenarios_df.loc[:, COLS].groupby(['kind', 'handle'])

fig_df = (grouper.agg(['median', 'mean', 'count', 'std'])
                 .dropna()
                 .amount_in_usdt
                 .stack()
                 .reset_index()
                 .rename(columns={'level_2': 'metric', 0: 'value'})
                 .query('value < 1_000'))

fig = px.histogram(fig_df,
                   x='value',
                   facet_row='kind',
                   facet_col='metric',
                   log_y=True,
                   title='Histogram for Aggregate Contribution per User and Scenario (log scale)',
                   height=600,
                   width=1000)

fig_2 = px.histogram(fig_df,
                   x='value',
                   facet_row='kind',
                   facet_col='metric',
                   log_y=True,
                   title='Density Histogram for Aggregate Contribution per User and Scenario (log scale)',
                   histnorm='probability density', 
                   height=600,
                   width=1000)

fig.show()
fig_2.show()

Total Contributions (original): 324324
Total Contributions (modified): 324324
Total Contributions (removed): 34358
___
Matched Contributions (original): 324324
Matched Contributions (modified): 289966
Matched Contributions (removed): 0
Change: 34358
Total Contributors (original): 17402
Total Contributors (modified): 15332
Total Contributors (removed): 2071
---
Sum of USDT Amount (original): 3317271.92
Sum of USDT Amount (removed): 153007.15
---
Median of Median USDT Amount per User (original): 1.41
Median of Median USDT Amount per User (modified): 1.40
Median of Median USDT Amount per User (removed): 1.48
---
Median Contribution Count per User (original): 12.00
Median Contribution Count per User (modified): 12.00
Median Contribution Count per User (removed): 12.00
---
Mean Count per User (original): 18.64
Mean Count per User (modified): 21.15
Mean Count per User (removed): 16.59
---
